In [7]:
# Import necessary modules
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.image as mpimg
from time import perf_counter
import os
from dtw import *
from pprint import pprint
import time
%matplotlib inline

print("> All necessary modules imported")

> All necessary modules imported


In [4]:
# Store features of genuine signatures for each writer --> Each writer has 5 genuine signatures

def storeSignaturesFeaturesOfEachAuthor(authorsFile, allSignaturesFolder):
    with open(authorsFile, 'r') as f:
        authorsList = []
        for line in f.readlines():
            authorsList.append(line.split(" ")[0].strip())
    print("> The list of authors is" + str(authorsList))
    
    authorSignatures = {}
    for author in authorsList:
        signaturesForOneAuthor = []
        for i in range(1, 6):
            signatureList = []
            with open(allSignaturesFolder+ author+"-g-0"+str(i)+".txt", "r") as signature:
                allWindows = signature.readlines()
                previous = {}
                for iteration, window in enumerate(allWindows):
                    line = window.split(" ")
                    line[6] = line[6].strip()
                    
                    # Get the values used to compute the features of each window
                    t = float(line[0])
                    x = float(line[1])
                    y = float(line[2])
                    pressure = float(line[3])
                    
                    if iteration==0:
                        vx = 0.0
                        vy = 0.0
                    else:
                        vx = float((x - previous['x']) / (t - previous['t']))
                        
                    # Store the previous values of the time, the x and y coordinatees to compute vx, vy at next iteration
                    previous['t'] = t
                    previous['x'] = x
                    previous['y'] = y
                    
                    signatureList.append([x, y, vx, vy, pressure])
                signaturesForOneAuthor.append(np.asarray(signatureList))
        authorSignatures[author] = signaturesForOneAuthor
    return authorSignatures            
                    
allGenuineSignatures = storeSignaturesFeaturesOfEachAuthor("./users.txt", "./enrollment/")

# test format -> test['user'][numberOfSignature][nth_window]
print("> All features of genuine signatures for each writer stored: " + str(allGenuineSignatures))

> The list of authors is['001', '002', '003', '004', '005', '006', '007', '008', '009', '010', '011', '012', '013', '014', '015', '016', '017', '018', '019', '020', '021', '022', '023', '024', '025', '026', '027', '028', '029', '030']
> All features of genuine signatures for each writer stored: {'001': [array([[  17.44,   80.24,    0.  ,    0.  ,   54.  ],
       [  19.11,   82.17,  167.  ,    0.  ,  146.  ],
       [  18.96,   82.41,  -15.  ,    0.  ,  314.  ],
       [  18.96,   82.49,    0.  ,    0.  ,  422.  ],
       [  18.96,   82.49,    0.  ,    0.  ,  504.  ],
       [  18.96,   82.42,    0.  ,    0.  ,  537.  ],
       [  18.96,   82.36,    0.  ,    0.  ,  556.  ],
       [  18.82,   82.21,  -14.  ,    0.  ,  592.  ],
       [  18.62,   80.99,  -20.  ,    0.  ,  610.  ],
       [  17.7 ,   79.08,  -92.  ,    0.  ,  608.  ],
       [  16.31,   76.41, -139.  ,    0.  ,  588.  ],
       [  14.61,   73.92, -170.  ,    0.  ,  535.  ],
       [  13.13,   71.55, -148.  ,    0.  ,  50

In [5]:
# Load verification data: 45 signatures per writer, 20 genuine and 25 forgeries
def storeVerificationSignature(verificationSignaturesFolder):
    authorSignatures ={}
    for fileName in os.listdir(verificationSignaturesFolder):
        with open(verificationSignaturesFolder+fileName, "r") as signature:
            allWindows = signature.readlines()
            previous = {}
            signatureList =[]
            for iteration, window in enumerate(allWindows):
                    line = window.split(" ")
                    line[6] = line[6].strip()
                    
                    # Get the values used to compute the features of each window
                    t = float(line[0])
                    x = float(line[1])
                    y = float(line[2])
                    pressure = float(line[3])
                    
                    if iteration==0:
                        vx = 0.0
                        vy = 0.0
                    else:
                        vx = float((x - previous['x']) / (t - previous['t']))
                        
                    # Store the previous values of the time, the x and y coordinatees to compute vx, vy at next iteration
                    previous['t'] = t
                    previous['x'] = x
                    previous['y'] = y
                    
                    signatureList.append([x, y, vx, vy, pressure])
        authorSignatures[fileName.replace(".txt", "")] = np.asarray(signatureList)
    return authorSignatures

verificationSignatures = storeVerificationSignature("./verification/")
pprint(verificationSignatures)
    

{'001-01': array([[  18.01,   15.92,    0.  ,    0.  ,  119.  ],
       [  19.62,   18.25,  161.  ,    0.  ,  170.  ],
       [  20.1 ,   18.9 ,   48.  ,    0.  ,  265.  ],
       [  20.41,   19.26,   31.  ,    0.  ,  382.  ],
       [  20.51,   19.42,   10.  ,    0.  ,  448.  ],
       [  20.51,   19.35,    0.  ,    0.  ,  491.  ],
       [  20.36,   19.23,  -15.  ,    0.  ,  546.  ],
       [  19.8 ,   18.24,  -56.  ,    0.  ,  581.  ],
       [  18.77,   16.7 , -103.  ,    0.  ,  589.  ],
       [  17.43,   14.51, -134.  ,    0.  ,  592.  ],
       [  15.83,   12.14, -160.  ,    0.  ,  595.  ],
       [  14.15,    9.66, -168.  ,    0.  ,  560.  ],
       [  12.42,    7.18, -173.  ,    0.  ,  544.  ],
       [  11.39,    5.78, -103.  ,    0.  ,  486.  ],
       [  11.1 ,    5.1 ,  -29.  ,    0.  ,  427.  ],
       [  11.29,    5.1 ,   19.  ,    0.  ,  418.  ],
       [  11.78,    5.71,   49.  ,    0.  ,  417.  ],
       [  13.07,    6.83,  129.  ,    0.  ,  422.  ],
       [  14.9 , 

 '002-01': array([[  87.5 ,    5.52,    0.  ,    0.  ,   53.  ],
       [  87.25,    4.88,  -25.  ,    0.  ,  301.  ],
       [  87.1 ,    4.69,  -15.  ,    0.  ,  382.  ],
       [  87.01,    4.62,   -9.  ,    0.  ,  469.  ],
       [  87.01,    4.62,    0.  ,    0.  ,  526.  ],
       [  87.17,    4.73,   16.  ,    0.  ,  610.  ],
       [  87.38,    4.95,   21.  ,    0.  ,  696.  ],
       [  87.68,    5.45,   30.  ,    0.  ,  754.  ],
       [  88.12,    6.14,   44.  ,    0.  ,  834.  ],
       [  88.65,    6.96,   53.  ,    0.  ,  908.  ],
       [  89.25,    8.04,   60.  ,    0.  ,  929.  ],
       [  89.79,    9.69,   54.  ,    0.  ,  947.  ],
       [  90.28,   11.72,   49.  ,    0.  ,  989.  ],
       [  90.82,   14.42,   54.  ,    0.  , 1023.  ],
       [  91.33,   16.13,   51.  ,    0.  , 1023.  ],
       [  91.6 ,   17.17,   27.  ,    0.  , 1023.  ],
       [  91.73,   17.82,   13.  ,    0.  , 1023.  ],
       [  91.73,   17.87,    0.  ,    0.  , 1023.  ],
       [  91.73, 

 '002-42': array([[  50.63,   62.19,    0.  ,    0.  ,  362.  ],
       [  50.55,   61.26,   -8.  ,    0.  ,  634.  ],
       [  50.55,   61.  ,    0.  ,    0.  ,  725.  ],
       [  50.55,   60.81,    0.  ,    0.  ,  831.  ],
       [  50.5 ,   60.67,   -5.  ,    0.  ,  941.  ],
       [  50.5 ,   60.67,    0.  ,    0.  , 1023.  ],
       [  50.55,   60.67,    5.  ,    0.  , 1023.  ],
       [  50.55,   60.67,    0.  ,    0.  , 1023.  ],
       [  50.55,   60.75,    0.  ,    0.  , 1023.  ],
       [  50.7 ,   60.99,   15.  ,    0.  , 1023.  ],
       [  51.14,   61.36,   44.  ,    0.  , 1023.  ],
       [  51.79,   62.28,   65.  ,    0.  , 1023.  ],
       [  52.51,   63.73,   72.  ,    0.  , 1023.  ],
       [  53.25,   65.54,   74.  ,    0.  , 1023.  ],
       [  53.76,   68.04,   51.  ,    0.  , 1023.  ],
       [  54.1 ,   70.61,   34.  ,    0.  , 1023.  ],
       [  54.54,   73.22,   44.  ,    0.  , 1023.  ],
       [  54.79,   74.07,   25.  ,    0.  , 1023.  ],
       [  54.9 , 

 '005-11': array([[  60.36,   25.16,    0.  ,    0.  ,  122.  ],
       [  60.13,   24.16,  -23.  ,    0.  ,  153.  ],
       [  59.92,   24.22,  -21.  ,    0.  ,  161.  ],
       [  59.74,   24.37,  -18.  ,    0.  ,  222.  ],
       [  59.66,   24.57,   -8.  ,    0.  ,  244.  ],
       [  59.66,   25.01,    0.  ,    0.  ,  277.  ],
       [  59.61,   25.71,   -5.  ,    0.  ,  311.  ],
       [  59.61,   26.58,    0.  ,    0.  ,  309.  ],
       [  59.61,   27.75,    0.  ,    0.  ,  324.  ],
       [  59.72,   28.84,   11.  ,    0.  ,  325.  ],
       [  59.96,   29.89,   24.  ,    0.  ,  325.  ],
       [  60.28,   30.44,   32.  ,    0.  ,  325.  ],
       [  60.44,   30.59,   16.  ,    0.  ,  314.  ],
       [  60.54,   30.47,   10.  ,    0.  ,  317.  ],
       [  60.61,   30.18,    7.  ,    0.  ,  324.  ],
       [  60.8 ,   29.71,   19.  ,    0.  ,  324.  ],
       [  61.01,   29.12,   21.  ,    0.  ,  324.  ],
       [  61.28,   28.6 ,   27.  ,    0.  ,  325.  ],
       [  61.62, 

       [ 116.28,   80.01,    0.  ,    0.  ,   83.  ]]),
 '006-19': array([[ 15.75,  62.25,   0.  ,   0.  ,  39.  ],
       [ 16.45,  62.54,  70.  ,   0.  , 103.  ],
       [ 16.84,  62.75,  39.  ,   0.  , 190.  ],
       ...,
       [ 44.9 ,  56.1 ,   0.  ,   0.  , 908.  ],
       [ 44.9 ,  56.1 ,   0.  ,   0.  , 713.  ],
       [ 44.9 ,  56.01,   0.  ,   0.  , 282.  ]]),
 '006-20': array([[ 18.74,  11.2 ,   0.  ,   0.  , 172.  ],
       [ 19.53,  11.35,  79.  ,   0.  , 329.  ],
       [ 19.81,  11.56,  28.  ,   0.  , 392.  ],
       ...,
       [ 48.09,  11.33,   0.  ,   0.  , 785.  ],
       [ 48.09,  11.33,   0.  ,   0.  , 570.  ],
       [ 48.09,  11.33,   0.  ,   0.  ,  54.  ]]),
 '006-21': array([[  54.44,   87.06,    0.  ,    0.  ,  141.  ],
       [  53.1 ,   87.23, -134.  ,    0.  ,  222.  ],
       [  52.19,   87.23,  -91.  ,    0.  ,  287.  ],
       ...,
       [  72.9 ,   86.77,  -12.  ,    0.  ,  514.  ],
       [  72.9 ,   86.83,    0.  ,    0.  ,  493.  ],
       [  72.

...

 '024-09': array([[  90.15,   24.37,    0.  ,    0.  ,  131.  ],
       [  89.93,   23.59,  -22.  ,    0.  ,  218.  ],
       [  89.84,   23.28,   -9.  ,    0.  ,  281.  ],
       [  89.84,   23.12,    0.  ,    0.  ,  345.  ],
       [  89.84,   23.07,    0.  ,    0.  ,  418.  ],
       [  89.9 ,   23.07,    6.  ,    0.  ,  501.  ],
       [  89.95,   23.13,    5.  ,    0.  ,  592.  ],
       [  90.04,   23.21,    9.  ,    0.  ,  684.  ],
       [  90.18,   23.46,   14.  ,    0.  ,  758.  ],
       [  90.43,   24.17,   25.  ,    0.  ,  797.  ],
       [  90.77,   25.19,   34.  ,    0.  ,  827.  ],
       [  91.15,   26.8 ,   38.  ,    0.  ,  824.  ],
       [  91.64,   28.9 ,   49.  ,    0.  ,  827.  ],
       [  92.21,   31.33,   57.  ,    0.  ,  805.  ],
       [  92.72,   33.66,   51.  ,    0.  ,  797.  ],
       [  92.99,   35.7 ,   27.  ,    0.  ,  791.  ],
       [  93.1 ,   36.9 ,   11.  ,    0.  ,  794.  ],
       [  93.05,   37.65,   -5.  ,    0.  ,  796.  ],
       [  92.96, 

       [111.1 ,  13.08, 279.  ,   0.  , 101.  ]]),
 '026-37': array([[ 12.53,  83.46,   0.  ,   0.  , 108.  ],
       [ 12.53,  83.46,   0.  ,   0.  , 181.  ],
       [ 12.53,  83.46,   0.  ,   0.  , 254.  ],
       ...,
       [ 39.07,  85.09, 243.  ,   0.  , 636.  ],
       [ 41.43,  85.8 , 236.  ,   0.  , 489.  ],
       [ 42.31,  86.03,  88.  ,   0.  , 173.  ]]),
 '026-38': array([[ 51.83,  75.21,   0.  ,   0.  , 119.  ],
       [ 51.83,  75.63,   0.  ,   0.  , 160.  ],
       [ 51.91,  75.91,   8.  ,   0.  , 237.  ],
       ...,
       [ 72.4 ,  81.57, 249.  ,   0.  , 783.  ],
       [ 74.61,  82.64, 221.  ,   0.  , 641.  ],
       [ 76.11,  83.45, 150.  ,   0.  , 247.  ]]),
 '026-39': array([[ 52.33,   9.83,   0.  ,   0.  ,  53.  ],
       [ 52.33,   9.44,   0.  ,   0.  , 245.  ],
       [ 52.19,   9.33, -14.  ,   0.  , 279.  ],
       ...,
       [ 76.44,  10.66,  28.  ,   0.  , 600.  ],
       [ 76.36,  10.66,  -8.  ,   0.  , 559.  ],
       [ 76.06,  10.61, -30.  ,   0.  , 338

       [  34.88,    6.05,  278.  ,    0.  ,  979.  ]]),
 '027-25': array([[  86.87,   60.84,    0.  ,    0.  ,  131.  ],
       [  86.48,   60.75,  -39.  ,    0.  ,  277.  ],
       [  86.24,   60.75,  -24.  ,    0.  ,  339.  ],
       [  86.15,   60.98,   -9.  ,    0.  ,  364.  ],
       [  86.15,   61.27,    0.  ,    0.  ,  405.  ],
       [  86.42,   61.62,   27.  ,    0.  ,  436.  ],
       [  86.84,   62.82,   42.  ,    0.  ,  458.  ],
       [  87.54,   63.92,   70.  ,    0.  ,  469.  ],
       [  88.43,   64.96,   89.  ,    0.  ,  477.  ],
       [  89.44,   65.98,  101.  ,    0.  ,  495.  ],
       [  90.41,   66.99,   97.  ,    0.  ,  504.  ],
       [  91.4 ,   67.84,   99.  ,    0.  ,  509.  ],
       [  92.43,   68.58,  103.  ,    0.  ,  505.  ],
       [  93.33,   68.95,   90.  ,    0.  ,  492.  ],
       [  94.13,   68.86,   80.  ,    0.  ,  489.  ],
       [  94.52,   68.46,   39.  ,    0.  ,  496.  ],
       [  94.52,   67.7 ,    0.  ,    0.  ,  509.  ],
       [  94.34

 '028-03': array([[  88.54,   26.3 ,    0.  ,    0.  ,  103.  ],
       [  87.94,   26.21,  -60.  ,    0.  ,  311.  ],
       [  87.41,   26.08,  -53.  ,    0.  ,  333.  ],
       [  86.75,   25.9 ,  -66.  ,    0.  ,  386.  ],
       [  86.34,   25.62,  -41.  ,    0.  ,  445.  ],
       [  86.2 ,   25.3 ,  -14.  ,    0.  ,  474.  ],
       [  86.2 ,   25.22,    0.  ,    0.  ,  464.  ],
       [  86.44,   25.11,   24.  ,    0.  ,  472.  ],
       [  87.02,   24.97,   58.  ,    0.  ,  488.  ],
       [  87.84,   24.97,   82.  ,    0.  ,  516.  ],
       [  89.18,   25.33,  134.  ,    0.  ,  544.  ],
       [  90.54,   25.93,  136.  ,    0.  ,  557.  ],
       [  91.92,   26.88,  138.  ,    0.  ,  560.  ],
       [  93.44,   28.04,  152.  ,    0.  ,  562.  ],
       [  94.92,   29.34,  148.  ,    0.  ,  543.  ],
       [  96.21,   30.44,  129.  ,    0.  ,  516.  ],
       [  97.38,   31.87,  117.  ,    0.  ,  496.  ],
       [  98.23,   33.51,   85.  ,    0.  ,  467.  ],
       [  98.58, 

       [ 113.34,   81.13,  598.  ,    0.  ,  933.  ]]),
 '028-22': array([[  17.02,   13.51,    0.  ,    0.  ,  220.  ],
       [  16.82,   12.72,  -20.  ,    0.  ,  246.  ],
       [  16.82,   12.67,    0.  ,    0.  ,  239.  ],
       [  17.01,   12.45,   19.  ,    0.  ,  246.  ],
       [  17.35,   12.23,   34.  ,    0.  ,  262.  ],
       [  17.78,   12.03,   43.  ,    0.  ,  289.  ],
       [  18.26,   12.03,   48.  ,    0.  ,  322.  ],
       [  18.95,   12.12,   69.  ,    0.  ,  351.  ],
       [  19.77,   12.47,   82.  ,    0.  ,  366.  ],
       [  20.85,   13.17,  108.  ,    0.  ,  366.  ],
       [  21.94,   14.1 ,  109.  ,    0.  ,  363.  ],
       [  23.02,   15.29,  108.  ,    0.  ,  317.  ],
       [  23.87,   16.67,   85.  ,    0.  ,  304.  ],
       [  24.59,   18.18,   72.  ,    0.  ,  276.  ],
       [  24.88,   19.52,   29.  ,    0.  ,  287.  ],
       [  24.69,   20.56,  -19.  ,    0.  ,  275.  ],
       [  24.19,   21.4 ,  -50.  ,    0.  ,  297.  ],
       [  23.4 

In [26]:
# Compute the average distanced between all genuine signatures for each writer
%load_ext autoreload
%autoreload 2
%reload_ext autoreload

def meanDistance(allGenuineSignatures):
    meanDistanceForEachAuthor = {}
    for author in allGenuineSignatures:
        allDistances = []
        for i in range(0, len(allGenuineSignatures[author])):
            for j in range(i+1, len(allGenuineSignatures[author])):
                # DOES NOT WORK BECAUSE THE SIGNATURES HAVE NOT THE SAME SIZE --> NEED TO NORMALIZE 
                dist = fastdtw(allGenuineSignatures[author][i], allGenuineSignatures[author][j])
                allDistances.append(dist)
        meanDistanceForEachAuthor[author] = np.mean(allDistances)
    return meanDistanceForEachAuthor

meanDistanceForEachAuthor = meanDistance(allGenuineSignatures)
print(meanDistanceForEachAuthor)
    
            


The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload
ts1:[[  17.44   80.24    0.      0.     54.  ]
 [  19.11   82.17  167.      0.    146.  ]
 [  18.96   82.41  -15.      0.    314.  ]
 [  18.96   82.49    0.      0.    422.  ]
 [  18.96   82.49    0.      0.    504.  ]
 [  18.96   82.42    0.      0.    537.  ]
 [  18.96   82.36    0.      0.    556.  ]
 [  18.82   82.21  -14.      0.    592.  ]
 [  18.62   80.99  -20.      0.    610.  ]
 [  17.7    79.08  -92.      0.    608.  ]
 [  16.31   76.41 -139.      0.    588.  ]
 [  14.61   73.92 -170.      0.    535.  ]
 [  13.13   71.55 -148.      0.    501.  ]
 [  12.03   69.86 -110.      0.    486.  ]
 [  11.18   69.05  -85.      0.    475.  ]
 [  10.86   68.82  -32.      0.    417.  ]
 [  10.92   69.12    6.      0.    397.  ]
 [  11.22   70.37   30.      0.    399.  ]
 [  12.02   72.26   80.      0.    420.  ]
 [  13.06   74.76  104.      0.    465.  ]
 [  14.26   77.35  120.      0.    502.  ]
 [  1

ts1:[[  17.44   80.24    0.      0.     54.  ]
 [  19.11   82.17  167.      0.    146.  ]
 [  18.96   82.41  -15.      0.    314.  ]
 [  18.96   82.49    0.      0.    422.  ]
 [  18.96   82.49    0.      0.    504.  ]
 [  18.96   82.42    0.      0.    537.  ]
 [  18.96   82.36    0.      0.    556.  ]
 [  18.82   82.21  -14.      0.    592.  ]
 [  18.62   80.99  -20.      0.    610.  ]
 [  17.7    79.08  -92.      0.    608.  ]
 [  16.31   76.41 -139.      0.    588.  ]
 [  14.61   73.92 -170.      0.    535.  ]
 [  13.13   71.55 -148.      0.    501.  ]
 [  12.03   69.86 -110.      0.    486.  ]
 [  11.18   69.05  -85.      0.    475.  ]
 [  10.86   68.82  -32.      0.    417.  ]
 [  10.92   69.12    6.      0.    397.  ]
 [  11.22   70.37   30.      0.    399.  ]
 [  12.02   72.26   80.      0.    420.  ]
 [  13.06   74.76  104.      0.    465.  ]
 [  14.26   77.35  120.      0.    502.  ]
 [  15.6    80.01  134.      0.    517.  ]
 [  16.46   81.42   86.      0.    529.  ]
 [  16.

ts1:[[ 1.617e+01  6.325e+01  0.000e+00  0.000e+00  1.700e+02]
 [ 1.770e+01  6.485e+01  1.530e+02  0.000e+00  2.570e+02]
 [ 1.785e+01  6.523e+01  1.500e+01  0.000e+00  3.440e+02]
 [ 1.759e+01  6.534e+01 -2.600e+01  0.000e+00  4.440e+02]
 [ 1.749e+01  6.526e+01 -1.000e+01  0.000e+00  4.880e+02]
 [ 1.719e+01  6.513e+01 -3.000e+01  0.000e+00  5.260e+02]
 [ 1.676e+01  6.421e+01 -4.300e+01  0.000e+00  5.430e+02]
 [ 1.553e+01  6.277e+01 -1.230e+02  0.000e+00  5.670e+02]
 [ 1.398e+01  6.049e+01 -1.550e+02  0.000e+00  5.600e+02]
 [ 1.222e+01  5.768e+01 -1.760e+02  0.000e+00  5.150e+02]
 [ 1.077e+01  5.453e+01 -1.450e+02  0.000e+00  4.660e+02]
 [ 9.490e+00  5.191e+01 -1.280e+02  0.000e+00  4.680e+02]
 [ 8.310e+00  5.066e+01 -1.180e+02  0.000e+00  4.610e+02]
 [ 8.260e+00  5.033e+01 -5.000e+00  0.000e+00  4.220e+02]
 [ 8.560e+00  5.052e+01  3.000e+01  0.000e+00  4.230e+02]
 [ 9.080e+00  5.181e+01  5.200e+01  0.000e+00  4.220e+02]
 [ 1.043e+01  5.384e+01  1.350e+02  0.000e+00  4.330e+02]
 [ 1.195e+

ts1:[[  19.62   30.54    0.      0.     71.  ]
 [  21.39   31.87  177.      0.    239.  ]
 [  21.45   32.27    6.      0.    304.  ]
 [  20.78   32.21  -67.      0.    410.  ]
 [  20.6    31.79  -18.      0.    464.  ]
 [  19.96   31.12  -64.      0.    512.  ]
 [  19.01   29.5   -95.      0.    537.  ]
 [  17.66   27.27 -135.      0.    551.  ]
 [  16.06   24.63 -160.      0.    541.  ]
 [  14.29   22.1  -177.      0.    499.  ]
 [  12.82   19.91 -147.      0.    466.  ]
 [  11.82   17.94 -100.      0.    458.  ]
 [  11.14   17.08  -68.      0.    422.  ]
 [  11.06   16.95   -8.      0.    391.  ]
 [  11.28   17.32   22.      0.    364.  ]
 [  11.71   18.63   43.      0.    369.  ]
 [  12.62   20.73   91.      0.    377.  ]
 [  13.89   23.35  127.      0.    398.  ]
 [  15.39   26.43  150.      0.    430.  ]
 [  17.47   29.71  208.      0.    467.  ]
 [  19.     33.13  153.      0.    510.  ]
 [  20.15   34.38  115.      0.    567.  ]
 [  20.23   34.73    8.      0.    611.  ]
 [  20.

C:\Users\Jojo\Anaconda\lib\site-packages\numpy\core\fromnumeric.py:2920: RuntimeWarning: Mean of empty slice.
  out=out, **kwargs)
C:\Users\Jojo\Anaconda\lib\site-packages\numpy\core\_methods.py:85: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)


ts1:[[  24.02   63.61    0.      0.      3.  ]
 [  24.02   63.61    0.      0.     63.  ]
 [  24.02   63.61    0.      0.     83.  ]
 [  24.02   63.61    0.      0.    108.  ]
 [  24.2    63.89   18.      0.    160.  ]
 [  24.13   63.89   -7.      0.    213.  ]
 [  24.     63.94  -13.      0.    244.  ]
 [  23.83   63.94  -17.      0.    301.  ]
 [  23.57   63.84  -26.      0.    344.  ]
 [  23.27   63.71  -30.      0.    346.  ]
 [  22.93   63.51  -34.      0.    356.  ]
 [  22.62   63.25  -31.      0.    371.  ]
 [  22.32   62.92  -30.      0.    373.  ]
 [  22.11   62.55  -21.      0.    368.  ]
 [  22.06   62.15   -5.      0.    361.  ]
 [  22.06   61.72    0.      0.    351.  ]
 [  22.34   61.22   28.      0.    348.  ]
 [  22.73   60.83   39.      0.    344.  ]
 [  23.31   60.51   58.      0.    341.  ]
 [  23.95   60.39   64.      0.    329.  ]
 [  24.78   60.45   83.      0.    307.  ]
 [  25.71   60.63   93.      0.    301.  ]
 [  26.67   60.96   96.      0.    291.  ]
 [  27.

ts1:[[   8.46   62.17    0.      0.     54.  ]
 [   8.46   62.17    0.      0.    107.  ]
 [   8.98   62.54   52.      0.    216.  ]
 ...
 [  14.76   62.27  401.      0.   1023.  ]
 [  20.52   65.14  576.      0.    944.  ]
 [  27.45   67.46  693.      0.    702.  ]]
ts2:[[  8.04  27.51   0.     0.   173.  ]
 [  8.04  27.51   0.     0.   314.  ]
 [  8.54  27.98  50.     0.   447.  ]
 ...
 [ 15.83  26.87 443.     0.   980.  ]
 [ 21.36  28.82 553.     0.   822.  ]
 [ 27.62  30.67 626.     0.   249.  ]]
m576n576
ts1:[[ 22.31  69.81   0.     0.    51.  ]
 [ 22.31  69.81   0.     0.    88.  ]
 [ 22.31  69.81   0.     0.   134.  ]
 ...
 [ 34.51  60.21 340.     0.   645.  ]
 [ 37.45  60.12 294.     0.   542.  ]
 [ 40.08  60.01 263.     0.   173.  ]]
ts2:[[ 20.51  35.71   0.     0.    56.  ]
 [ 20.51  35.71   0.     0.   142.  ]
 [ 20.51  35.71   0.     0.   195.  ]
 ...
 [ 42.05  23.57 163.     0.   687.  ]
 [ 43.01  23.4   96.     0.   567.  ]
 [ 43.53  23.3   52.     0.   314.  ]]
m224n224


ts1:[[  15.07   60.12    0.      0.    279.  ]
 [  15.07   60.12    0.      0.    327.  ]
 [  15.07   60.12    0.      0.    299.  ]
 [  14.61   60.36  -46.      0.    294.  ]
 [  14.54   60.84   -7.      0.    307.  ]
 [  14.64   61.56   10.      0.    344.  ]
 [  14.86   62.43   22.      0.    389.  ]
 [  15.31   63.58   45.      0.    441.  ]
 [  15.96   64.86   65.      0.    498.  ]
 [  16.73   66.22   77.      0.    512.  ]
 [  17.43   67.23   70.      0.    541.  ]
 [  18.14   67.92   71.      0.    527.  ]
 [  18.81   68.41   67.      0.    513.  ]
 [  19.44   68.76   63.      0.    507.  ]
 [  20.02   68.86   58.      0.    489.  ]
 [  20.54   68.79   52.      0.    495.  ]
 [  21.01   68.34   47.      0.    491.  ]
 [  21.25   67.5    24.      0.    463.  ]
 [  21.1    66.41  -15.      0.    391.  ]
 [  20.68   65.02  -42.      0.    364.  ]
 [  20.     63.62  -68.      0.    381.  ]
 [  19.14   62.26  -86.      0.    415.  ]
 [  18.16   61.19  -98.      0.    448.  ]
 [  17.

{'001': 449411.1499946793, '002': nan, '003': 7796433.259876375, '004': nan, '005': nan, '006': nan, '007': nan, '008': 1456293.6735330452, '009': 18180173.6910842, '010': 3062888.167438059, '011': nan, '012': nan, '013': nan, '014': nan, '015': nan, '016': 99518.51437439253, '017': nan, '018': nan, '019': 4127928.7122222856, '020': nan, '021': nan, '022': nan, '023': 630656.6646275874, '024': nan, '025': nan, '026': nan, '027': 853057.2191053834, '028': nan, '029': 306715.7640060606, '030': nan}
